<style>
    h1{ font-family:"Times New Roman",serif;
        color:darkorange;
        background-color:black;
        text-align:center;
        text-shadow:2px 2px 0px red, 0 0 5px silver;
        border: #ffa000 solid 5px;
        height:1.5em;
    }
    h2{ font-weight: ;
    }
</style>
<h1> I-PHOQS Laboratory Training Platform </h1>
 <h2> <b>Preliminary: Image Pre-processing </b></h2>
<h><i> Notebook developed by Federico Avella and Luca Labate</i> <h>

In [65]:
#%% Import relevant modules
import importlib
import numpy as np
import matplotlib.pyplot as plt
import cv2
import glob

from importnb import imports

In [ ]:
#%% Import the AuxiliaryClass
with imports("ipynb"):
    import AuxiliaryTools as at
    importlib.reload(at) 

ac = at.AuxiliaryClass()
mm = 1e-3

<h2> Input and output parameters </h2>
<ul>
    <li> <strong>Nimages</strong>: number of input images (corresponding to the number of positions where the images were taken </li>
    <li> <strong>pixelsizex, pixelsizey</strong>: size of the pixel of the original images along x and y</li>
    <li> <strong>resampligFactor</strong>: for the sake of keeping the size (in memory) of each image at a reasonable level, a sampling of the original image(s) to reduce the number of pixels might be needed. This factor corresponds to the fraction of pixels (along each direction) which are kept. For instance, a resamplingFactor=0.5 corresponds to 1 out of 2 pixels being kept (and 1 every other pixel being dropped)</li>
    <li> <strong>finalImageNpixelsx, finalImageNpixelsy</strong>: number of pixels in the final images, that is, the images obtained after the resampling and the centering of the images to each other (using the center of mass as a reference)</li>
    <li> <strong>InputDIR, InputImage1FN, InputImage2FN</strong>, ...: self-explanatory</li>
</ul>

<h2><li> Set the input parameters (dir names, file names, etc.) and the output parameters</li></h2>

In [ ]:
InputDIR = "./source_imgs"
imagesFNs = glob.glob("*.tif",root_dir=InputDIR)
imagesFNs.sort()

pixelsizex = 0.005*mm # in mm
pixelsizey = 0.005*mm # in mm
resamplingFactor = float(input("Enter the resampling factor (e.g., 0.5 for half size): "))

finalImageNpixelsx = int(input("Enter the number of pixels in x direction for the final image: "))
finalImageNpixelsy = int(input("Enter the number of pixels in y direction for the final image: "))


<h2><li>  Retrieve internal params and allocate objects </li></h2> 

In [ ]:
ac.setImagesDir(InputDIR)
ac.setImagesFilenames(*imagesFNs)

resampledpixelsizex = pixelsizex / resamplingFactor
resampledpixelsizey = pixelsizey / resamplingFactor

xMin = resampledpixelsizex/2.0
xMax = resampledpixelsizex * (finalImageNpixelsx - 0.5)
yMin = resampledpixelsizey/2.0
yMax = resampledpixelsizey * (finalImageNpixelsy - 0.5)


xCoord = np.linspace(xMin, xMax, finalImageNpixelsx)
yCoord = np.linspace(yMin, yMax, finalImageNpixelsy)

xExtent = resampledpixelsizex/2.0 + np.max(xCoord)
yExtent = resampledpixelsizey/2.0 + np.max(yCoord)

print("Final image actual size: {:f}, {:f}".format(xExtent, yExtent))

<h2><li> Allocate an ImageClass for each image and then load the image </li></h2>
<h3>Show the original image</h3>
<par><strong>WARNING</strong>: on executing the following cell, you should close each of the images you will be shown with by typing 'q'.<br>
Closing the image using the mouse might result in the notebook getting frozen</par>

In [ ]:
inputImages = [at.ImageClass() for i in ac.imagesPath]
for i,img in enumerate(inputImages):
    img.loadImage(ac.imagesPath[i],{'x':pixelsizex,'y':pixelsizey})
for img in inputImages:
    img.showOriginal()

<h3>Select the color channel of interest</h3>

In [ ]:
#%% Select the red (or other) channel
for i in range(len(inputImages)):
    inputImages[i].selectChannel("R")

<h2><li> Resample the original image </li></h2>
<par><strong>WARNING</strong>: again, as before!</par>

In [19]:

for img in inputImages:
    img.resampleOriginal(factor=resamplingFactor)
    img.showOriginal()

>>	Original shape: (2616, 3896)
>>	Resampled shape: (1308, 1948). New calibration: {'y': 0.01, 'x': 0.01}
>>	Original shape: (2616, 3896)
>>	Resampled shape: (1308, 1948). New calibration: {'y': 0.01, 'x': 0.01}
>>	Original shape: (2616, 3896)
>>	Resampled shape: (1308, 1948). New calibration: {'y': 0.01, 'x': 0.01}


<h2><li> Select Region Of Interest and BackGround for each istance in inputImages </li></h2>

<par><strong>WARNING 1</strong>: for each image you will select ROI and BG in sequence. Look at window name ;)<br>
<strong>WARNING 2</strong>: in order to select the ROI/BG of each image</par>
<ol>
 <li> Use the mouse to select the ROI by holding the left button pressed</li>
 <li> Press the spacebar with the button still pressed</li>
 <li>close the image by pressing 'q'</li>
</ol>

In [ ]:
for img in inputImages:
    img.selectROI()
    img.selectBG()
# Subtract a background from the ROI
    img.retrieveAverageBG()
    img.subtractBGfromROI()

### You can resample the ROI image with: 
```python
ROIresampling = True
```

In [ ]:
#%% Show the background-corrected ROIs
ROIresampling = False
resROIfactor = 1/resamplingFactor
for img in inputImages:
    if ROIresampling:
        img.resampleROI(factor=resROIfactor)
    else:
        pass

<h4>Check the BG level after subtraction</h4> 

In [ ]:
for img in inputImages:
    winName = f"Check {img.imageName} ROI background"
    cv2.namedWindow(winName, cv2.WINDOW_NORMAL)
    ROIedges = cv2.selectROI(winName, img.ROI, True, False)
    tmp = img.ROI[ROIedges[1]:ROIedges[1]+ROIedges[3], ROIedges[0]:ROIedges[0]+ROIedges[2]]
    tmp_avr_bg = np.mean(tmp)
# Subtract a background from the ROI
    print(img.imageName+' BG value after correction: '+str(tmp_avr_bg))
    cv2.destroyWindow(winName)


<style>
    code{color:white}
</style>
<h2><li> Create the final, centered images </li></h2>
<h3> <strong>WARNING</strong>: the number of pixels in both axis-directions (y:0,x:1) must be higher than the ROI shape </h3>
<p> The method <code>.buildImageWithSize()</code> extends the images along both axis up to the provided number of pixels, adding 0-value padding.</p>
<p> Then it centers the image according to <code>.getCenterOfMassOfROI()</code></p> 

In [ ]:
#%% Retrieve the center of mass
for img in inputImages:
    img.getCenterOfMassOfROI()
    img.buildImageWithSize(finalImageNpixelsx,finalImageNpixelsy)
    img.showCenteredROI()


<h>Show the final images as density maps with matplotlib</h>

In [ ]:
Nimages=len(inputImages)
fig, ax = plt.subplots(1, Nimages, figsize=(12,4*Nimages))

for i in range(Nimages):
    Ny,Nx = inputImages[i].ysize,inputImages[i].xsize
    yMax = (Ny+.5)*inputImages[i].roiCalibration['y']
    xMax = (Nx+.5)*inputImages[i].roiCalibration['x']
    img=ax[i].imshow(inputImages[i].centeredROI,
              extent=np.array([0, xMax, 0, yMax])*1e3,
              cmap='RdBu_r',
              aspect='equal',
              vmin=0,
              vmax=255)
    ax[i].set_xlabel('x [mm]')
    ax[i].set_ylabel('y [mm]')
    ax[i].set_title(inputImages[i].imageName)
    plt.colorbar(img,shrink=.3)
    print(inputImages[i].imageName,
          'shape: '+str(inputImages[i].centeredROI.shape),
          'calibration: '+str(inputImages[i].roiCalibration),
          "xMax = {:.2f}, yMax = {:.2f}".format(xMax,yMax),
          sep="\n\t-",
          end="\n")
fig.tight_layout()

<h2>Demonstration of other auxiliary functions <h2>

<h3>Enhancing contrast <h3>

In [60]:
ShowAuxFunctions = input("Do you want to show the auxiliary functions? (y/n) ").lower()
if ShowAuxFunctions[0]=='y':
    immagine = inputImages[0].enhanceContrast(inputImages[0].ROI,2)
    cv2.namedWindow("fig2", cv2.WINDOW_NORMAL)
    cv2.namedWindow("fig3", cv2.WINDOW_NORMAL)
    cv2.imshow("fig2", inputImages[0].ROI)
    cv2.imshow("fig3", immagine)
    cv2.waitKey(0)
    cv2.destroyWindow("fig2")
    cv2.destroyWindow("fig3")

<h3> Rescaling Max/Min values <h3>

In [ ]:
if ShowAuxFunctions[0]=='y':
    fig, ax = plt.subplots(1, Nimages, figsize=(12,4*Nimages))
    
    for i in range(Nimages):
        img=inputImages[i]
        Ny,Nx = inputImages[i].ysize,inputImages[i].xsize
        yMax = (Ny+1)*inputImages[i].roiCalibration['y']
        xMax = (Nx+1)*inputImages[i].roiCalibration['x']
        image=ax[i].imshow(img.rescale2minmax(img.centeredROI,0,1),
                  extent=[0, xMax, 0, yMax],cmap='RdBu_r',aspect='equal')
        ax[i].set_xlabel('x [mm]')
        ax[i].set_ylabel('y [mm]')
        plt.colorbar(image,shrink=.3)
    